<a href="https://colab.research.google.com/github/rlskoeser/shxco-missingdata-specreading/blob/main/missing-data/Sco_prophet_missingdata_weekly.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Predict Missing Members Data from Shakespeare and Company Project

This notebook explores and predicts missing data related to members. It contains the code for figures 4, 5, and 6 in our paper.

## Setup Libraries and Load S&Co Data



In [66]:
import warnings
warnings.filterwarnings('ignore')
import altair as alt
alt.data_transformers.disable_max_rows()


import sys
sys.path.append('..')

from utils.missing_data_processing import *
from utils.forecasting_missing_data import *

In [67]:
events_df, _, _, _  = load_initial_data()
logbook_events_df = generate_logbooks_events(events_df)
membership_events = generate_member_events(events_df)
logbook_gaps_df, logbooks_weekly_count, logbook_gaps, logbook_events_nogaps = generate_logbook_gaps(logbook_events_df)
member_events, newmember_yearly_count, members_first_dates = generate_member_events(events_df)
members_first_events = member_events.groupby("member_id").first().reset_index()
newmember_subscriptions_by_year, newmember_subscriptions_by_week = generate_newmember_subscriptions(member_events, logbook_gaps)
subscription_first_events = member_events[member_events.source_type.str.contains('Logbook') & member_events.event_type.isin(['Subscription', 'Renewal'])].groupby("member_id").first().reset_index()

The 6 large gaps in the logbooks
	January 01 1928 to February 29 1928 (59 days)
	January 03 1930 to June 01 1930 (149 days)
	August 01 1930 to December 31 1930 (152 days)
	February 17 1931 to September 25 1932 (586 days)
	January 01 1937 to February 16 1938 (411 days)
	May 06 1938 to October 20 1938 (167 days)

The 5 small gaps in the logbooks that will be skipped
	October 30 1927 to November 01 1927 (2 days)
	February 07 1934 to February 08 1934 (1 day)
	January 01 1935 to January 11 1935 (10 days)
	December 29 1935 to January 01 1936 (3 days)
	August 29 1939 to September 12 1939 (14 days)


## Missing member events

In our first notebook, we explored predicting missing membership activities, but we can also predict missing member data. We will use the same approach as before, but this time we will predict the number of members who had subscriptions.

### Generate logbook / membership events by week

We will first generate our previous chart that shows the number of membership activities in logbooks along with gaps.

In [68]:
base = alt.Chart(logbooks_weekly_count).encode(
    alt.X('logbook_date:T', axis=alt.Axis(title='date'))
).properties(
    width=1200,
    height=275
)

line = base.mark_line().encode(
    alt.Y('total',
          axis=alt.Axis(title='total events per week'))
)
# draw rectangles to highlight logbook gaps
logbook_gaps_span = alt.Chart(logbook_gaps_df).encode(
     alt.X('start')
).properties(
    width=1200,
    height=275
).mark_rect(
    opacity=0.2, color="gray"
).encode(
    x='start',
    x2='end',
    y=alt.value(0),  # 0 pixels from bottom
    y2=alt.value(275)  # 300 pixels from top
)


line + logbook_gaps_span

alt.LayerChart(...)

### Visualize member data

To visualize this pattern, we will plot the number of new members by year based on their unique member id.

In [80]:
# This chart shows the number of new members by year, along with the logbook gaps
newmember_base = alt.Chart(newmember_yearly_count, title='new members by year').encode(
    alt.X('date:T', axis=alt.Axis(title='date'))
).properties(
    width=1200,
    height=275
)

newmember_line = newmember_base.mark_line().encode(
    alt.Y('total',
          axis=alt.Axis(title='new members by year'))
)
newmember_line + logbook_gaps_span

alt.LayerChart(...)

In [71]:
# Confirm the number of rows in the df == the number of unique members included

print(f"Number of rows in members_first_events: {len(members_first_events)}")
print(f"Number of unique members in members_first_events: {len(members_first_events.member_id.unique())}")
print(f"These numbers should be the same. If they are not, there are duplicates in the data.")

Number of rows in members_first_events: 5085
Number of unique members in members_first_events: 5085
These numbers should be the same. If they are not, there are duplicates in the data.


In [72]:
# What is the breakdown of event types for first events?
members_first_events.event_type.value_counts()

Subscription        4189
Renewal              550
Reimbursement        208
Borrow                91
Purchase              18
Separate Payment      12
Supplement            10
Gift                   3
Crossed out            1
Request                0
Name: event_type, dtype: int64

In [73]:
# What about source of first events
members_first_events.source_type.value_counts()

Logbook                                      2744
Logbook;Address Book                         1375
Address Book                                  445
Logbook;Lending Library Card                  242
Lending Library Card                          220
Lending Library Card;Address Book              22
Logbook;Lending Library Card;Address Book      19
Lending Library Card;Logbook                   15
Lending Library Card;Lending Library Card       2
Lending Library Card;Logbook;Address Book       1
Name: source_type, dtype: int64

### Explore new members added from logbooks only

So far, we have looked at all members, but we can also look at new members added from logbooks only. This will help us understand the number of new members added each year as a proxy of the number of members who had subscriptions.

In [74]:
# Get first events for each member from logbooks only
# Go back to member events, limit to logbook events, then group and get first event
logbook_first_events = member_events[member_events.source_type.str.contains('Logbook')].groupby("member_id").first().reset_index()


In [76]:
# Confirm one row per member
print(f"Number of rows in logbook_first_events: {len(logbook_first_events)}")
print(f"Number of unique members in logbook_first_events: {len(logbook_first_events.member_id.unique())}")
print(f"These numbers should be the same. If they are not, there are duplicates in the data.")

Number of rows in logbook_first_events: 4597
Number of unique members in logbook_first_events: 4597
These numbers should be the same. If they are not, there are duplicates in the data.


In [77]:
# Check source type breakdown
logbook_first_events.source_type.value_counts()

Logbook                                              2828
Logbook;Address Book                                 1412
Logbook;Lending Library Card                          309
Logbook;Lending Library Card;Address Book              25
Lending Library Card;Logbook                           20
Logbook;Lending Library Card;Lending Library Card       1
Logbook;Address Book;Lending Library Card               1
Lending Library Card;Logbook;Address Book               1
Name: source_type, dtype: int64

##### Aggregate new members by year

In [78]:
# We aim to get the yearly count of new members based solely on logbook-sourced events.

# We start by grouping the 'logbook_first_events' DataFrame by year. 
# The 'pd.Grouper' function is used with the key set to 'date' and the frequency set to 'Y' for yearly grouping.
# For each group, we count the number of unique 'member_id' values. This gives us the number of new members for each year.
logbook_newmembers_by_year = logbook_first_events.groupby([pd.Grouper(key='date', freq='Y')])['member_id'].count().reset_index()

# We then rename the 'member_id' column to 'total' for clarity. 
# The 'total' column now represents the total number of new members for each year.
logbook_newmembers_by_year.rename(columns={'member_id': 'total'}, inplace=True)

logbook_newmembers_by_year

date  total
0  1919-12-31     53
1  1920-12-31    193
2  1921-12-31    278
3  1922-12-31    322
4  1923-12-31    280
5  1924-12-31    325
6  1925-12-31    404
7  1926-12-31    436
8  1927-12-31    296
9  1928-12-31    289
10 1929-12-31    283
11 1930-12-31     33
12 1931-12-31     22
13 1932-12-31     78
14 1933-12-31    240
15 1934-12-31    105
16 1935-12-31    212
17 1936-12-31    183
18 1937-12-31      1
19 1938-12-31    112
20 1939-12-31    173
21 1940-12-31    125
22 1941-12-31    154

In [79]:
# We aim to create a line chart that shows the number of new members by year.

# We start by creating a base chart from the 'logbook_newmembers_by_year' DataFrame. 
# The 'date' column is mapped to the x-axis.
# We also set the width and height of the chart.
logbook_newmember_base = alt.Chart(logbook_newmembers_by_year, title='new members by year').encode(
    alt.X('date:T', axis=alt.Axis(title='date'))
).properties(
    width=1200,
    height=275
)

# We then create a line chart by marking the base chart with lines.
# The 'total' column is mapped to the y-axis. The line color is set to purple.
logbook_newmember_line = logbook_newmember_base.mark_line(color="purple").encode(
    alt.Y('total',
          axis=alt.Axis(title='new members by year'))
)

# Finally, we overlay the new line chart on top of the existing 'newmember_line' chart.
newmember_line + logbook_newmember_line

alt.LayerChart(...)

##### Aggregate by month instead of year

In [86]:
# Get new member monthly count for logbook-sourced events only 
logbook_newmembers_by_month = logbook_first_events.groupby([pd.Grouper(key='date', freq='M')])['member_id'].count().reset_index()
logbook_newmembers_by_month.rename(columns={'member_id': 'total'}, inplace=True)

logbook_newmember_monthly_base = alt.Chart(logbook_newmembers_by_month, title='New members by month from logbooks only').encode(
    alt.X('date:T', axis=alt.Axis(title='date'))
).properties(
    width=1200,
    height=275
)

logbook_newmember_monthly_line = logbook_newmember_monthly_base.mark_line(color="purple", opacity=0.5).encode(
    alt.Y('total',
          axis=alt.Axis(title='New members by month'))
)

logbook_newmember_monthly_line

alt.Chart(...)

In [87]:
newmember_monthly_count = members_first_dates.groupby([pd.Grouper(key='date', freq='M')])['member_id'].count().reset_index()
newmember_monthly_count.rename(columns={'member_id': 'total'}, inplace=True)

newmember_monthly_base = alt.Chart(newmember_monthly_count, title='New members by month from all sources').encode(
    alt.X('date:T', axis=alt.Axis(title='date'))
).properties(
    width=1200,
    height=275
)

newmember_monthly_line = newmember_monthly_base.mark_line(opacity=0.5).encode(
    alt.Y('total',
          axis=alt.Axis(title='new members by month'))
)

newmember_monthly_line

alt.Chart(...)

### Members only documented in address books

In [88]:
# We are trying to identify members who are only known from the address books.

# We start by identifying members who have at least one event recorded in the logbooks.
# We do this by filtering the 'member_events' DataFrame to include only logbook events, 
# and then getting the unique 'member_id' values.
logbook_members = member_events[member_events.source_type.str.contains('Logbook')].member_id.unique()

# Similarly, we identify members who have at least one event recorded on a lending library card.
lending_card_members = member_events[member_events.source_type.str.contains('Lending Library Card')].member_id.unique()

# We also identify members who have at least one event recorded in an address book.
addressbook_members = member_events[member_events.source_type.str.contains('Address Book')].member_id.unique()

# We then get a list of members who only have events from the address books.
# We do this by subtracting the sets of logbook members and lending card members from the set of all members.
address_book_only_members = set(member_events.member_id.unique()) - set(logbook_members) - set(lending_card_members)

# Finally, we print the number of members who only have events from the address books.
print('%d members who only have events from the address books' % len(address_book_only_members))

329 members who only have events from the address books


In [90]:
# We aim to get the date when each member who only has events from the address books was first added.

# We start by filtering the 'member_events' DataFrame to include only events for members who only have events from the address books.
# We then group the filtered DataFrame by 'member_id' and select the first event for each member.
# This gives us the first event for each member who only has events from the address books.
addressbook_first_events = member_events[member_events.member_id.isin(address_book_only_members)].groupby("member_id").first().reset_index()

# We aim to get the yearly count of new members who only have events from the address books.

# We group the 'addressbook_first_events' DataFrame by year. 
# The 'pd.Grouper' function is used with the key set to 'date' and the frequency set to 'Y' for yearly grouping.
# For each group, we count the number of unique 'member_id' values. This gives us the number of new members for each year.
addressbook_newmembers_by_year = addressbook_first_events.groupby([pd.Grouper(key='date', freq='Y')])['member_id'].count().reset_index()

# We then rename the 'member_id' column to 'total' for clarity. 
# The 'total' column now represents the total number of new members for each year.
addressbook_newmembers_by_year.rename(columns={'member_id': 'total'}, inplace=True)

# Finally, we print the total number of new members who only have events from the address books.
addressbook_newmembers_by_year.total.sum()

329

### Members only documented on lending cards

In [91]:
# We aim to identify members who only have events recorded on a lending library card.

# We start by getting a list of all unique member IDs from the 'member_events' DataFrame.
# We then subtract the sets of logbook members and address book members from this list.
# This gives us a list of members who only have events recorded on a lending library card.
lending_card_only_members = set(member_events.member_id.unique()) - set(logbook_members) - set(addressbook_members)

# Finally, we print the number of members who only have events from lending library cards.
print('%d members who only have events from lending library cards' % len(lending_card_only_members))

124 members who only have events from lending library cards


In [92]:
cardonly_members = member_events[member_events.member_id.isin(lending_card_only_members)]
cardonly_members['year'] = cardonly_members.date.apply(lambda x: x.year)
cardonly_members.year.unique()

array([1919, 1920, 1922, 1923, 1924, 1925, 1927, 1928, 1929, 1930, 1931,
       1932, 1933, 1934, 1935, 1936, 1937, 1938, 1939, 1940, 1941])

In [93]:
# We generate the date when each member who only has events from lending library cards was first added. We start by filtering the 'member_events' DataFrame to include only events for members who only have events from lending library cards. We then group the filtered DataFrame by 'member_id' and select the first event for each member.
# This gives us the first event for each member who only has events from lending library cards.
cardonly_first_events = member_events[member_events.member_id.isin(lending_card_only_members)].groupby("member_id").first().reset_index()

# We aim to get the yearly count of new members who only have events from lending library cards.

# We group the 'cardonly_first_events' DataFrame by year. 
# The 'pd.Grouper' function is used with the key set to 'date' and the frequency set to 'Y' for yearly grouping.
# For each group, we count the number of unique 'member_id' values. This gives us the number of new members for each year.
cardonly_newmembers_by_year = cardonly_first_events.groupby([pd.Grouper(key='date', freq='Y')])['member_id'].count().reset_index()

# We then rename the 'member_id' column to 'total' for clarity. 
# The 'total' column now represents the total number of new members for each year.
cardonly_newmembers_by_year.rename(columns={'member_id': 'total'}, inplace=True)

### Other members

In [94]:
# We finally want to identify "regular" members, i.e., members who have events recorded in sources other than just the address books or lending library cards.

# We start by getting a list of all unique member IDs from the 'member_events' DataFrame.
# We then subtract the sets of lending card only members and address book only members from this list.
# This gives us a list of "regular" members.
other_members = set(member_events.member_id.unique()) - set(lending_card_only_members) - set(address_book_only_members)

# Finally, we print the number of "regular" members.
print('%d "regular" members (not addressbook or lending card only)' % len(other_members))

4632 "regular" members (not addressbook or lending card only)


In [95]:
# We get the date when each "regular" member was first added. We start by filtering the 'member_events' DataFrame to include only events for "regular" members. We then group the filtered DataFrame by 'member_id' and select the first event for each member. This gives us the first event for each "regular" member.
other_member_first_events = member_events[member_events.member_id.isin(other_members)].groupby("member_id").first().reset_index()

# We also get the yearly count of new "regular" members.

# We group the 'other_member_first_events' DataFrame by year. 
# The 'pd.Grouper' function is used with the key set to 'date' and the frequency set to 'Y' for yearly grouping.
# For each group, we count the number of unique 'member_id' values. This gives us the number of new "regular" members for each year.
other_newmembers_by_year = other_member_first_events.groupby([pd.Grouper(key='date', freq='Y')])['member_id'].count().reset_index()

# We then rename the 'member_id' column to 'total' for clarity. 
# The 'total' column now represents the total number of new "regular" members for each year.
other_newmembers_by_year.rename(columns={'member_id': 'total'}, inplace=True)

In [96]:
# Finally we combine the yearly counts of new members from different categories into a single DataFrame for plotting.

def combine_newmember_counts():
  # We start by creating copies of the 'other_newmembers_by_year', 'addressbook_newmembers_by_year', and 'cardonly_newmembers_by_year' DataFrames.
  # We add a new column 'series' to each DataFrame to indicate the category of the new members.
  other_newmembers = other_newmembers_by_year.copy()
  other_newmembers['series'] = 'all other members'

  addressbook_newmembers = addressbook_newmembers_by_year.copy()
  addressbook_newmembers['series'] = 'addressbook-only members'
  
  card_newmembers = cardonly_newmembers_by_year.copy()
  card_newmembers['series'] = 'card-only members'
  
  # We then concatenate the three DataFrames into a single DataFrame.
  # This combined DataFrame can be used for plotting with Altair.
  combined_new_member_counts_df = pd.concat([other_newmembers, addressbook_newmembers, card_newmembers])

  # We return the combined DataFrame.
  return combined_new_member_counts_df

# We call the function to get the combined DataFrame.
combine_newmember_counts_df = combine_newmember_counts()

### Aggregate new members from source by month

In [97]:
# get new member monthly count for addressbook-only members events only 
addressbook_newmembers_by_month = addressbook_first_events.groupby([pd.Grouper(key='date', freq='M')])['member_id'].count().reset_index()
addressbook_newmembers_by_month.rename(columns={'member_id': 'total'}, inplace=True)

# get new member monthly count for lending card-only members
cardonly_newmembers_by_month = cardonly_first_events.groupby([pd.Grouper(key='date', freq='M')])['member_id'].count().reset_index()
cardonly_newmembers_by_month.rename(columns={'member_id': 'total'}, inplace=True)

# new member monthly count 
other_newmembers_by_month = other_member_first_events.groupby([pd.Grouper(key='date', freq='M')])['member_id'].count().reset_index()
other_newmembers_by_month.rename(columns={'member_id': 'total'}, inplace=True)

In [98]:
# We combine the monthly counts of new members from different categories into a single DataFrame for plotting.
def combine_newmember_monthly_counts():
  # We start by creating copies of the 'other_newmembers_by_month', 'addressbook_newmembers_by_month', and 'cardonly_newmembers_by_month' DataFrames.
  # We add a new column 'series' to each DataFrame to indicate the category of the new members.
  other_newmembers = other_newmembers_by_month.copy()
  other_newmembers['series'] = 'all other members'

  addressbook_newmembers = addressbook_newmembers_by_month.copy()
  addressbook_newmembers['series'] = 'addressbook-only members'
  
  card_newmembers = cardonly_newmembers_by_month.copy()
  card_newmembers['series'] = 'card-only members'
  
  # We then concatenate the three DataFrames into a single DataFrame.
  # This combined DataFrame can be used for plotting with Altair.
  combined_new_member_counts_df = pd.concat([other_newmembers, addressbook_newmembers, card_newmembers])

  # We return the combined DataFrame.
  return combined_new_member_counts_df

# We call the function to get the combined DataFrame.
combine_newmember_monthly_counts_df = combine_newmember_monthly_counts()

In [99]:
domain = ['addressbook-only members', 'card-only members', 'all other members']
range_ = ['#d7191c', '#fdae61', '#2c7bb6']

newmember_monthly_stacked = alt.Chart(combine_newmember_monthly_counts_df, title='New members by source, aggregated by month').mark_area(opacity=0.5).encode(
    x="date:T",
    y="total",
    color=alt.Color("series", legend=alt.Legend(title="member group"), scale=alt.Scale(domain=domain, range=range_))
).properties(
    width=1200,
    height=275
)

#### Figure - New members by month, based on source. (Blue line: new members by month from any source; purple line: new members based on logbook data only, i.e. first logbook events for members).

In [100]:
newmember_monthly_stacked + newmember_monthly_line + logbook_newmember_monthly_line + logbook_gaps_span

alt.LayerChart(...)

## New members by first subscription

In [38]:
# To model membership activities accurately, we expect a membership to start with a 'Subscription' or 'Renewal' event. 
# This is because in the logbooks, 'Subscription' and 'Renewal' events were sometimes recorded interchangeably.

# We start by filtering the 'member_events' DataFrame to include only events recorded in the logbooks 
# and where the 'event_type' is either 'Subscription' or 'Renewal'.
filtered_member_events = member_events[member_events.source_type.str.contains('Logbook') & member_events.event_type.isin(['Subscription', 'Renewal'])]

# We then group the filtered DataFrame by 'member_id' and select the first event for each member.
# This gives us the first 'Subscription' or 'Renewal' event for each member.
subscription_first_events = filtered_member_events.groupby("member_id").first().reset_index()

In [40]:
# We exclude any subscriptions that fall within the gaps in the logbooks.

# We start by creating a copy of the 'subscription_first_events' DataFrame. 
# This is to ensure that we don't modify the original DataFrame when excluding gaps.
subscription_first_events_nogaps = subscription_first_events.copy()

# We then iterate over each gap in 'logbook_gaps'.
for i, gap in enumerate(logbook_gaps):
  # We extract the start and end dates of the current gap.
  gap_start = gap['start']
  gap_end = gap['end']

  # We filter 'subscription_first_events_nogaps' to exclude any events that fall within the current gap.
  # This is done by excluding events where the 'date' is between 'gap_start' and 'gap_end'.
  subscription_first_events_nogaps = subscription_first_events_nogaps[~((subscription_first_events_nogaps.date >= gap_start) & (subscription_first_events_nogaps.date <= gap_end))]

# Finally, we count the number of unique 'member_id' values in 'subscription_first_events_nogaps'.
# This gives us the number of members whose first event does not fall within any of the gaps.
len(subscription_first_events_nogaps.member_id.unique())

4315

In [41]:
# We generate a yearly count of new members based solely on subscriptions, excluding gaps.

# We start by grouping the 'subscription_first_events_nogaps' DataFrame by year. 
# The 'pd.Grouper' function is used with the key set to 'date' and the frequency set to 'Y' for yearly grouping.
# For each group, we count the number of unique 'member_id' values. This gives us the number of new members for each year.
newmember_subscriptions_by_year = subscription_first_events_nogaps.groupby([pd.Grouper(key='date', freq='Y')])['member_id'].count().reset_index()

# We then rename the 'member_id' column to 'total' for clarity. 
# The 'total' column now represents the total number of new members for each year.
newmember_subscriptions_by_year.rename(columns={'member_id': 'total'}, inplace=True)

In [42]:
# We generate a weekly count of new members based solely on subscriptions. 
# This data will be used for forecasting with the Prophet library.

# We start by grouping the 'subscription_first_events_nogaps' DataFrame by week. 
# The 'pd.Grouper' function is used with the key set to 'date' and the frequency set to 'W' for weekly grouping.
# For each group, we count the number of unique 'member_id' values. This gives us the number of new members for each week.
newmember_subscriptions_by_week = subscription_first_events_nogaps.groupby([pd.Grouper(key='date', freq='W')])['member_id'].count().reset_index()

# We then rename the 'member_id' column to 'total' for clarity. 
# The 'total' column now represents the total number of new members for each week.
newmember_subscriptions_by_week.rename(columns={'member_id': 'total'}, inplace=True)

In [43]:
# We create a line chart that shows the number of new subscriptions per week, with gaps.

# We start by creating a base chart from the 'newmember_subscriptions_by_week' DataFrame. 
# The 'date' column is mapped to the x-axis.
# We also set the width and height of the chart.
newsubs_base = alt.Chart(newmember_subscriptions_by_week).encode(
    alt.X('date:T', axis=alt.Axis(title='date'))
).properties(
    width=1200,
    height=275
)

# We then create a line chart by marking the base chart with lines.
# The 'total' column is mapped to the y-axis. This represents the number of new subscriptions per week.
newsubs_line = newsubs_base.mark_line().encode(
    alt.Y('total',
          axis=alt.Axis(title='new subscriptions per week'))
)

# Finally, we overlay the new line chart on top of the 'logbook_gaps_span' chart.
# This allows us to visualize the gaps in the logbooks alongside the number of new subscriptions per week.
newsubs_line + logbook_gaps_span

alt.LayerChart(...)

### Use prophet to forecast missing subscriptions

#### Figure - New member subscriptions from logbooks by week, with forecast model and predictions (linear model, weekly seasonality enabled).

In [44]:
post1932_date = pd.to_datetime(date(1932, 9, 27))
# Assuming `weekly_subscriptions` and `logbook_gaps` are defined elsewhere
forecasted_subscriptions = forecast_missing_subscriptions(newmember_subscriptions_by_week, logbook_gaps, post1932_date)

17:30:12 - cmdstanpy - INFO - Chain [1] start processing
17:30:12 - cmdstanpy - INFO - Chain [1] done processing
17:30:13 - cmdstanpy - INFO - Chain [1] start processing
17:30:13 - cmdstanpy - INFO - Chain [1] done processing
17:30:13 - cmdstanpy - INFO - Chain [1] start processing
17:30:13 - cmdstanpy - INFO - Chain [1] done processing
17:30:13 - cmdstanpy - INFO - Chain [1] start processing
17:30:13 - cmdstanpy - INFO - Chain [1] done processing
17:30:13 - cmdstanpy - INFO - Chain [1] start processing
17:30:13 - cmdstanpy - INFO - Chain [1] done processing
17:30:14 - cmdstanpy - INFO - Chain [1] start processing
17:30:14 - cmdstanpy - INFO - Chain [1] done processing


In [45]:
chart_height = 275
gap_areas = plot_gap_areas(logbook_gaps, chart_height, newmember_subscriptions_by_week, include_line=False)
plot_newsubs_weekly_forecast(forecasted_subscriptions, gap_areas, logbook_gaps, chart_height, post1932_date, newmember_subscriptions_by_week, show_model=True, separate_model_decades=False)

alt.LayerChart(...)

#### Figure - New member subscriptions from logbooks by week, with forecast model and predictions (logistic growth model, weekly seasonality enabled).

In [46]:
lognewsub_weeks_fcst = forecast_missing_subscriptions(newmember_subscriptions_by_week, logbook_gaps, post1932_date, train_all_data=True, return_prophet_model=False, use_weekly_growth_cap=True, use_total_growth_cap=True)

17:30:21 - cmdstanpy - INFO - Chain [1] start processing
17:30:21 - cmdstanpy - INFO - Chain [1] done processing
17:30:21 - cmdstanpy - INFO - Chain [1] start processing
17:30:22 - cmdstanpy - INFO - Chain [1] done processing
17:30:22 - cmdstanpy - INFO - Chain [1] start processing
17:30:22 - cmdstanpy - INFO - Chain [1] done processing
17:30:22 - cmdstanpy - INFO - Chain [1] start processing
17:30:22 - cmdstanpy - INFO - Chain [1] done processing
17:30:23 - cmdstanpy - INFO - Chain [1] start processing
17:30:23 - cmdstanpy - INFO - Chain [1] done processing
17:30:24 - cmdstanpy - INFO - Chain [1] start processing
17:30:24 - cmdstanpy - INFO - Chain [1] done processing
17:30:24 - cmdstanpy - INFO - Chain [1] start processing
17:30:24 - cmdstanpy - INFO - Chain [1] done processing


In [47]:
chart_height = 275
gap_areas = plot_gap_areas(logbook_gaps, chart_height, newmember_subscriptions_by_week, include_line=False)
plot_newsubs_weekly_forecast(lognewsub_weeks_fcst, gap_areas, logbook_gaps, chart_height, post1932_date, newmember_subscriptions_by_week, show_model=True, separate_model_decades=False)

alt.LayerChart(...)

## Simpler missing member estimate


To give us a comparison for Prophet, we will also use a simpler method to estimate the number of missing members. We will use the average number of new members per month from the logbooks to estimate the number of missing members. This is a simpler method than Prophet, but it will give us a comparison to see how well Prophet is able to predict the number of missing members.

In [48]:
# We start by getting the total number of unique member URIs in 'events_df' and 'logbook_events_df'.
# This gives us the total number of accounts and the total number of accounts from logbooks.
total_accounts = len(events_df.member_uris.unique())
total_logbook_accounts = len(logbook_events_df.member_uris.unique())

# We also get the total number of logbook events.
total_logbook_events = logbook_events_df.shape[0]

# We calculate the average number of new accounts per logbook event.
n_accounts_per_logbook_event = total_logbook_accounts / total_logbook_events

# We estimate the total number of logbook events based on external data.
# The estimates are provided as a range with an upper and lower bound.
est_total_logbook_events = 13955
est_total_logbook_events_upper = 15220
est_total_logbook_events_lower = 12358

# We estimate the total number of accounts from logbooks by multiplying the estimated total number of logbook events
# by the average number of new accounts per logbook event.
est_logbook_accounts = est_total_logbook_events * n_accounts_per_logbook_event
est_logbook_accounts_upper = est_total_logbook_events_upper * n_accounts_per_logbook_event
est_logbook_accounts_lower = est_total_logbook_events_lower * n_accounts_per_logbook_event

# We calculate the estimated number of missing accounts by subtracting the total number of accounts
# from the estimated total number of accounts from logbooks.
n_missing_accounts = int(est_logbook_accounts - total_accounts)
n_missing_accounts_upper = int(est_logbook_accounts_upper - total_accounts)
n_missing_accounts_lower = int(est_logbook_accounts_lower - total_accounts)

# We calculate the percentage of surviving accounts by dividing the total number of accounts
# by the estimated total number of accounts from logbooks.
percent_surviving_accounts = (total_accounts / est_logbook_accounts) * 100
percent_surviving_accounts_upper = (total_accounts / est_logbook_accounts_upper) * 100
percent_surviving_accounts_lower = (total_accounts / est_logbook_accounts_lower) * 100

# We print the results.
print("""
total accounts: %d
total accounts from logbooks: %d:
total logbook events: %d
new member per logbook event: %.2f
est total members from logbooks: %.2f (upper %.2f, lower %.2f)
est missing accounts: %.2f (upper %.2f, lower %.2f)
percent covered: %.2f (upper %.2f, lower %.2f)
""" % (
    total_accounts,
    total_logbook_accounts,
    total_logbook_events,
    n_accounts_per_logbook_event,
    est_logbook_accounts, est_logbook_accounts_upper, est_logbook_accounts_lower,
    n_missing_accounts, n_missing_accounts_upper, n_missing_accounts_lower,
    percent_surviving_accounts, percent_surviving_accounts_upper, percent_surviving_accounts_lower
))


total accounts: 5139
total accounts from logbooks: 4604:
total logbook events: 11601
new member per logbook event: 0.40
est total members from logbooks: 5538.21 (upper 6040.24, lower 4904.42)
est missing accounts: 399.00 (upper 901.00, lower -234.00)
percent covered: 92.79 (upper 85.08, lower 104.78)
percent missing: 



In [52]:
def simple_missing_member_est_collapsed():
  # We start by grouping the events by member names instead of member IDs.
  # This gives us the total number of unique accounts and the total number of unique accounts from logbooks.
  total_accounts = len(events_df.member_names.unique())
  total_logbook_accounts = len(logbook_events_df.member_names.unique())

  # We also get the total number of logbook events.
  total_logbook_events = logbook_events_df.shape[0]

  # We calculate the average number of new accounts per logbook event.
  n_accounts_per_logbook_event = total_logbook_accounts / total_logbook_events

  # We estimate the total number of logbook events based on external data.
  # The estimates are provided as a range with an upper and lower bound.
  est_total_logbook_events = 13955
  est_total_logbook_events_upper = 15220
  est_total_logbook_events_lower = 12358

  # We estimate the total number of accounts from logbooks by multiplying the estimated total number of logbook events
  # by the average number of new accounts per logbook event.
  est_logbook_accounts = est_total_logbook_events * n_accounts_per_logbook_event
  est_logbook_accounts_upper = est_total_logbook_events_upper * n_accounts_per_logbook_event
  est_logbook_accounts_lower = est_total_logbook_events_lower * n_accounts_per_logbook_event

  # We calculate the estimated number of missing accounts by subtracting the total number of accounts
  # from the estimated total number of accounts from logbooks.
  n_missing_accounts = int(est_logbook_accounts - total_accounts)
  n_missing_accounts_upper = int(est_logbook_accounts_upper - total_accounts)
  n_missing_accounts_lower = int(est_logbook_accounts_lower - total_accounts)

  # We calculate the percentage of surviving accounts by dividing the total number of accounts
  # by the estimated total number of accounts from logbooks.
  percent_surviving_accounts = (total_accounts / est_logbook_accounts) * 100
  percent_surviving_accounts_upper = (total_accounts / est_logbook_accounts_upper) * 100
  percent_surviving_accounts_lower = (total_accounts / est_logbook_accounts_lower) * 100

  # We print the results.
  print("""
  ** counting by unique name instead of member id**
  total accounts: %d
  total accounts from logbooks: %d:
  total logbook events: %d
  new member per logbook event: %.2f
  est total members from logbooks: %.2f (upper %.2f, lower %.2f)
  est missing accounts: %.2f (upper %.2f, lower %.2f)
  percent covered: %.2f (upper %.2f, lower %.2f)
  """ % (
      total_accounts,
      total_logbook_accounts,
      total_logbook_events,
      n_accounts_per_logbook_event,
      # est total members
      est_logbook_accounts, est_logbook_accounts_upper, est_logbook_accounts_lower,
      n_missing_accounts, n_missing_accounts_upper, n_missing_accounts_lower,
      percent_surviving_accounts, percent_surviving_accounts_upper, percent_surviving_accounts_lower
  ))

simple_missing_member_est_collapsed()


  ** counting by unique name instead of member id**
  total accounts: 4720
  total accounts from logbooks: 4200:
  total logbook events: 11601
  new member per logbook event: 0.36
  est total members from logbooks: 5052.24 (upper 5510.21, lower 4474.06)
  est missing accounts: 332.00 (upper 790.00, lower -245.00)
  percent covered: 93.42 (upper 85.66, lower 105.50)
  
